# Urban Area Analysis

This notebook calculates urban areas using population density, building footprints, and road network data.
The analysis uses a region-growing algorithm to identify contiguous urban areas.

## Methodology
1. Load population density hexagons, building footprints, and road networks
2. Aggregate building and road metrics per hexagon
3. Apply region-growing algorithm starting from highest-scoring seed cell
4. Visualize and save results

## Configuration

In [1]:
# === CONFIGURATION ===
CITY_NAME = "Oslo, Norway"  # e.g., "Paris, France", "Stockholm, Sweden", "London, England"
CITY_SHORT_NAME = CITY_NAME.split(',')[0].lower()  # Used for filenames/layers
TARGET_CRS = "EPSG:27393"  # NGO 1948 / Norway zone 3 is 27393

# File paths
BOUNDARIES_PATH = r"D:/Public Transport Study/Input Data/Boundaries/Boundaries.gpkg"
DATA_DIR = "./data"

print(f"Analyzing city: {CITY_NAME} ({CITY_SHORT_NAME})")
print(f"Using target CRS: {TARGET_CRS}")

Analyzing city: Oslo, Norway (oslo)
Using target CRS: EPSG:27393


## Imports and Setup

In [2]:
# Import required libraries
import geopandas as gpd
import osmnx as ox
import numpy as np
import pandas as pd
from tqdm import tqdm
import fiona
import folium
from pathlib import Path
from IPython.display import display
import warnings

# Suppress warnings for cleaner output
warnings.filterwarnings('ignore')

# Create data directory if it doesn't exist
Path(DATA_DIR).mkdir(exist_ok=True)

print(f"OSMnx version: {ox.__version__}")
print(f"GeoPandas version: {gpd.__version__}")

OSMnx version: 2.0.2
GeoPandas version: 1.0.1


## Data Loading Functions

In [3]:
def load_city_boundary(city_name, boundaries_path, target_crs):
    """Load and reproject city boundary from geopackage."""
    print(f"Loading city boundary for {city_name}...")
    
    cities = gpd.read_file(boundaries_path, layer="cities_used")
    cities = cities.to_crs(target_crs)
    
    city_boundary = cities[cities["Name"] == city_name]
    if city_boundary.empty:
        raise ValueError(f"City '{city_name}' not found in boundaries")
    
    print(f"City boundary loaded and reprojected to {target_crs}")
    return city_boundary


def load_or_query_buildings(city_name, city_short_name, target_crs, city_boundary, data_dir):
    """Load buildings from cache or query from OSM."""
    buildings_path = Path(data_dir) / "building_footprints.gpkg"
    layer_name = f"{city_short_name}_buildings"
    
    # Check if cached buildings exist
    try:
        layers = fiona.listlayers(str(buildings_path))
        if layer_name in layers:
            print(f"Loading cached buildings for {city_name}...")
            buildings = gpd.read_file(str(buildings_path), layer=layer_name)
            if buildings.crs != target_crs:
                buildings = buildings.to_crs(target_crs)
            
            # Ensure area column exists
            if 'area_sqm' not in buildings.columns:
                buildings['area_sqm'] = buildings.geometry.area
            
            print(f"Loaded {len(buildings)} cached buildings")
            return buildings
    except fiona.errors.DriverError:
        pass
    
    # Query from OSM
    print(f"Querying OSM for buildings in {city_name}...")
    query_polygon = city_boundary.to_crs("EPSG:4326")['geometry'].values[0]
    buildings_4326 = ox.features_from_polygon(query_polygon, tags={'building': True})
    buildings = buildings_4326.to_crs(target_crs)
    buildings['area_sqm'] = buildings.geometry.area
    
    # Cache the results
    try:
        buildings.to_file(str(buildings_path), layer=layer_name, driver="GPKG")
        print(f"Cached buildings to {buildings_path}")
    except Exception as e:
        print(f"Warning: Could not cache buildings: {e}")
    
    print(f"Queried {len(buildings)} buildings from OSM")
    return buildings


def load_or_query_roads(city_name, city_short_name, target_crs, city_boundary, data_dir):
    """Load roads from cache or query from OSM."""
    roads_path = Path(data_dir) / "road_networks.gpkg"
    layer_name = f"{city_short_name}_roads"
    
    # Check if cached roads exist
    try:
        layers = fiona.listlayers(str(roads_path))
        if layer_name in layers:
            print(f"Loading cached roads for {city_name}...")
            roads = gpd.read_file(str(roads_path), layer=layer_name)
            if roads.crs != target_crs:
                roads = roads.to_crs(target_crs)
            
            # Ensure length column exists
            if 'length_m' not in roads.columns:
                roads['length_m'] = roads.geometry.length
            
            print(f"Loaded {len(roads)} cached road segments ({roads['length_m'].sum()/1000:.1f} km)")
            return roads
    except fiona.errors.DriverError:
        pass
    
    # Query from OSM
    print(f"Querying OSM for roads in {city_name}...")
    query_polygon = city_boundary.to_crs("EPSG:4326")['geometry'].values[0]
    
    road_types = {
        'highway': ['motorway', 'trunk', 'primary', 'secondary', 'tertiary',
                   'unclassified', 'residential', 'motorway_link', 'trunk_link',
                   'primary_link', 'secondary_link', 'tertiary_link']
    }
    
    roads_4326 = ox.features_from_polygon(query_polygon, tags=road_types)
    roads_4326 = roads_4326[roads_4326.geometry.type == 'LineString']
    roads = roads_4326.to_crs(target_crs)
    roads['length_m'] = roads.geometry.length
    
    # Prepare for caching
    roads_clean = roads[['geometry', 'highway', 'name', 'length_m']].copy()
    for col in ['highway', 'name']:
        if col in roads_clean.columns:
            roads_clean[col] = roads_clean[col].astype(str).replace('nan', None)
    
    # Cache the results
    try:
        roads_clean.to_file(str(roads_path), layer=layer_name, driver="GPKG")
        print(f"Cached roads to {roads_path}")
    except Exception as e:
        print(f"Warning: Could not cache roads: {e}")
    
    print(f"Queried {len(roads_clean)} road segments ({roads_clean['length_m'].sum()/1000:.1f} km)")
    return roads_clean


def load_population_data(city_name, data_dir):
    """Load and filter population density data."""
    print(f"Loading population density data for {city_name}...")
    
    pop_path = Path(data_dir) / "population_density.gpkg"
    boundary_path = Path(data_dir) / "urban_areas.gpkg"
    
    population_data = gpd.read_file(str(pop_path), layer="population_density_cities_used")
    city_boundaries = gpd.read_file(str(boundary_path), layer="cities_used")
    
    city_boundary = city_boundaries[city_boundaries["Name"] == city_name]
    if city_boundary.empty:
        raise ValueError(f"Boundary for city '{city_name}' not found")
    
    # Ensure CRS compatibility
    if population_data.crs != city_boundary.crs:
        population_data = population_data.to_crs(city_boundary.crs)
    
    # Filter to city area
    pop_filtered = gpd.overlay(population_data, city_boundary, how='intersection')
    pop_filtered['hex_id'] = range(len(pop_filtered))
    
    print(f"Filtered to {len(pop_filtered)} population hexagons")
    return pop_filtered

## Spatial Analysis Functions

In [4]:
def aggregate_buildings_to_hexagons(buildings, hexagons):
    """Aggregate building statistics per hexagon."""
    print("Aggregating building data to hexagons...")
    
    # Ensure compatible CRS and valid geometries
    if buildings.crs != hexagons.crs:
        buildings = buildings.to_crs(hexagons.crs)
    
    buildings = buildings[buildings.geom_type.isin(["Polygon", "MultiPolygon"])]
    buildings = buildings[buildings.geometry.is_valid]
    hexagons = hexagons[hexagons.geometry.is_valid].copy()
    
    if buildings.empty:
        print("No valid buildings found")
        hexagons['total_building_area_sqm'] = 0.0
        hexagons['building_count'] = 0
        return hexagons
    
    # Spatial overlay and aggregation
    buildings['building_id'] = range(len(buildings))
    overlay = gpd.overlay(
        buildings[['building_id', 'geometry']],
        hexagons,
        how="intersection",
        keep_geom_type=False
    )
    
    overlay['intersected_area_sqm'] = overlay.geometry.area
    building_stats = overlay.groupby('hex_id').agg({
        'intersected_area_sqm': 'sum',
        'building_id': pd.Series.nunique
    }).rename(columns={
        'intersected_area_sqm': 'total_building_area_sqm',
        'building_id': 'building_count'
    })
    
    # Merge back to hexagons
    result = hexagons.merge(building_stats, on='hex_id', how='left')
    result['total_building_area_sqm'] = result['total_building_area_sqm'].fillna(0)
    result['building_count'] = result['building_count'].fillna(0).astype(int)
    
    print(f"Aggregated {result['building_count'].sum()} buildings")
    return result


def aggregate_roads_to_hexagons(roads, hexagons):
    """Aggregate road statistics per hexagon."""
    print("Aggregating road data to hexagons...")
    
    # Ensure compatible CRS and valid geometries
    if roads.crs != hexagons.crs:
        roads = roads.to_crs(hexagons.crs)
    
    roads = roads[roads.geometry.is_valid].copy()
    hexagons = hexagons.copy()
    
    if roads.empty:
        print("No valid roads found")
        hexagons['total_road_length_m'] = 0.0
        hexagons['road_density_km_per_sqkm'] = 0.0
        return hexagons
    
    # Spatial overlay and aggregation
    roads['road_id'] = range(len(roads))
    overlay = gpd.overlay(
        roads[['road_id', 'geometry']],
        hexagons,
        how="intersection",
        keep_geom_type=False
    )
    
    overlay['intersected_length_m'] = overlay.geometry.length
    road_stats = overlay.groupby('hex_id').agg({
        'intersected_length_m': 'sum',
        'road_id': pd.Series.nunique
    }).rename(columns={
        'intersected_length_m': 'total_road_length_m',
        'road_id': 'road_segment_count'
    })
    
    # Merge back and calculate density
    result = hexagons.merge(road_stats, on='hex_id', how='left')
    result['total_road_length_m'] = result['total_road_length_m'].fillna(0)
    result['road_segment_count'] = result['road_segment_count'].fillna(0).astype(int)
    
    # Calculate road density (km per sq km)
    hex_area_sqm = result.geometry.iloc[0].area
    hex_area_sqkm = hex_area_sqm / 1_000_000
    result['road_density_km_per_sqkm'] = (result['total_road_length_m'] / 1000) / hex_area_sqkm
    
    total_road_km = result['total_road_length_m'].sum() / 1000
    avg_density = result['road_density_km_per_sqkm'].mean()
    print(f"Aggregated {total_road_km:.1f} km of roads (avg density: {avg_density:.2f} km/sq km)")
    return result

## Load Data

In [5]:
# Load city boundary
city_boundary = load_city_boundary(CITY_NAME, BOUNDARIES_PATH, TARGET_CRS)

# Load buildings
city_buildings = load_or_query_buildings(
    CITY_NAME, CITY_SHORT_NAME, TARGET_CRS, city_boundary, DATA_DIR
)

# Load roads
city_roads = load_or_query_roads(
    CITY_NAME, CITY_SHORT_NAME, TARGET_CRS, city_boundary, DATA_DIR
)

# Load population data
population_hexagons = load_population_data(CITY_NAME, DATA_DIR)

print("\nData loading complete:")
print(f"- Buildings: {len(city_buildings):,}")
print(f"- Roads: {len(city_roads):,} segments")
print(f"- Population hexagons: {len(population_hexagons):,}")

Loading city boundary for Oslo, Norway...
City boundary loaded and reprojected to EPSG:27393
Loading cached buildings for Oslo, Norway...
Loaded 319285 cached buildings
Loading cached roads for Oslo, Norway...
Loaded 27325 cached road segments (4948.7 km)
Loading population density data for Oslo, Norway...
Filtered to 2450 population hexagons

Data loading complete:
- Buildings: 319,285
- Roads: 27,325 segments
- Population hexagons: 2,450


## Spatial Analysis

In [6]:
# Aggregate building data
analysis_data = aggregate_buildings_to_hexagons(city_buildings, population_hexagons)

# Aggregate road data
analysis_data = aggregate_roads_to_hexagons(city_roads, analysis_data)

# Prepare for urban detection
analysis_data = analysis_data.rename(columns={'hex_id': 'cell_id'})
analysis_data = analysis_data.to_crs(TARGET_CRS)

print(f"\nAnalysis dataset ready: {len(analysis_data)} hexagons with aggregated metrics")

Aggregating building data to hexagons...
Aggregated 330797 buildings
Aggregating road data to hexagons...
Aggregated 9374.4 km of roads (avg density: 9.41 km/sq km)

Analysis dataset ready: 2450 hexagons with aggregated metrics


## Data Visualization

In [ ]:
# Create interactive visualization
print("Creating interactive map...")

viz_data = analysis_data.to_crs("EPSG:4326")

# Calculate quantiles for tooltip display
viz_data['pop_quantile'] = (viz_data['population'].rank(pct=True) * 100).round(0).astype(int)
viz_data['building_quantile'] = (viz_data['total_building_area_sqm'].rank(pct=True) * 100).round(0).astype(int)
if 'road_density_km_per_sqkm' in viz_data.columns:
    viz_data['road_quantile'] = (viz_data['road_density_km_per_sqkm'].rank(pct=True) * 100).round(0).astype(int)

# Round values for cleaner tooltips
viz_data['population_rounded'] = viz_data['population'].round(0).astype(int)
viz_data['building_count_rounded'] = viz_data['building_count'].astype(int)
viz_data['building_area_rounded'] = viz_data['total_building_area_sqm'].round(0).astype(int)

# Calculate building coverage percentage
hex_area_sqm = analysis_data.geometry.iloc[0].area
viz_data['building_coverage_pct'] = (viz_data['total_building_area_sqm'] / hex_area_sqm * 100).round(0).astype(int)

if 'road_density_km_per_sqkm' in viz_data.columns:
    viz_data['road_density_rounded'] = viz_data['road_density_km_per_sqkm'].round(0).astype(int)
    viz_data['road_length_rounded'] = viz_data['total_road_length_m'].round(0).astype(int)

# Prepare tooltip columns with quantiles and rounded values
tooltip_cols = [
    "population_rounded", "pop_quantile",
    "building_count_rounded", "building_area_rounded", "building_quantile", 
    "building_coverage_pct"
]

if 'road_density_km_per_sqkm' in viz_data.columns:
    tooltip_cols.extend([
        "road_density_rounded", "road_quantile", "road_length_rounded"
    ])

# Create background layer with all analysis cells
all_cells_viz = analysis_data.to_crs("EPSG:4326")
# Add quantiles and rounded values for tooltips
all_cells_viz['pop_quantile'] = (all_cells_viz['population'].rank(pct=True) * 100).round(0).astype(int)
all_cells_viz['building_quantile'] = (all_cells_viz['total_building_area_sqm'].rank(pct=True) * 100).round(0).astype(int)
if 'road_density_km_per_sqkm' in all_cells_viz.columns:
    all_cells_viz['road_quantile'] = (all_cells_viz['road_density_km_per_sqkm'].rank(pct=True) * 100).round(0).astype(int)
all_cells_viz['population_display'] = all_cells_viz['population'].round(0).astype(int)
all_cells_viz['building_area_display'] = all_cells_viz['total_building_area_sqm'].round(0).astype(int)
if 'road_density_km_per_sqkm' in all_cells_viz.columns:
    all_cells_viz['road_density_display'] = all_cells_viz['road_density_km_per_sqkm'].round(0).astype(int)

# Tooltip for all analysis cells
all_cells_tooltip = [
    "population_display", "pop_quantile",
    "building_area_display", "building_quantile"
]
if 'road_density_km_per_sqkm' in all_cells_viz.columns:
    all_cells_tooltip.extend(["road_density_display", "road_quantile"])

# Create base map with all analysis cells (background layer, hidden by default)
m = all_cells_viz.explore(
    color="lightgrey",
    tooltip=all_cells_tooltip,
    popup=False,
    style_kwds=dict(
        fillColor="lightgrey",
        color="darkgrey", 
        fillOpacity=0.5,
        weight=1,
        opacity=0.8
    ),
    name="All Analysis Cells"
)

# Add population layer (default)
viz_data.explore(
    m=m,  # Add to existing map
    column="population",
    cmap="viridis",
    tooltip=tooltip_cols,
    popup=True,
    legend=True,
    legend_kwds=dict(caption="Population"),
    style_kwds=dict(fillOpacity=0.7, weight=0.5),
    name="Population Density"
)

# Add building density layer
viz_data.explore(
    m=m,  # Add to existing map
    column="total_building_area_sqm",
    cmap="plasma",
    tooltip=tooltip_cols,
    popup=True,
    legend=True,
    legend_kwds=dict(caption="Building Area (m²)"),
    style_kwds=dict(fillOpacity=0.7, weight=0.5),
    name="Building Density"
)

# Add road density layer if available
if 'road_density_km_per_sqkm' in viz_data.columns:
    viz_data.explore(
        m=m,  # Add to existing map
        column="road_density_km_per_sqkm",
        cmap="inferno",
        tooltip=tooltip_cols,
        popup=True,
        legend=True,
        legend_kwds=dict(caption="Road Density (km/sq km)"),
        style_kwds=dict(fillOpacity=0.7, weight=0.5),
        name="Road Density"
    )

# Add layer control to switch between layers
folium.LayerControl().add_to(m)

print(f"Interactive map created with {len(tooltip_cols)} tooltip fields")
print("Layers available:")
print("- Population Density (default)")
print("- Building Density")
if 'road_density_km_per_sqkm' in viz_data.columns:
    print("- Road Density")

display(m)

Creating interactive map...
Interactive map created


## Urban Area Detection Algorithm

In [ ]:
# Urban area detection algorithm with adjustable parameters
def run_growing_method(density, urban_strictness="medium"):
    """
    Fast contiguous urban area detection using breadth-first search
    
    Args:
    - density: GeoDataFrame with urban metrics (population, total_building_area_sqm, road_density_km_per_sqkm)
    - urban_strictness: "strict", "medium", or "loose" - controls how selective the algorithm is
    """
    print(f"Running enhanced growing method (strictness: {urban_strictness})...")
    
    # Import required libraries for fast processing
    from collections import deque
    import numpy as np
    
    # Check if road density is available
    has_road_density = 'road_density_km_per_sqkm' in density.columns
    use_road_density = (urban_strictness == "strict" and has_road_density)
    
    metrics_list = "population, building area"
    if use_road_density:
        metrics_list += ", road density"
    
    print(f"Using {'3' if use_road_density else '2'} metrics: {metrics_list}")
    
    # Ensure valid geometries and add unique IDs
    density = density[density.geometry.is_valid].copy()
    density['hex_id'] = range(len(density))
    
    # Calculate cell area for normalization (assuming hexagons are similar size)
    cell_area_sq_km = density.geometry.iloc[0].area / 1_000_000
    
    # Define strictness-based parameters using your quantile approach
    strictness_params = {
        "strict": {
            "pop_quantile": 0.05,  # Top 5% population (95th percentile)
            "building_quantile": 0.05,  # Top 5% building coverage
            "road_quantile": 0.10 if use_road_density else 0.90,
            "combined_min": 0.35
        },
        "medium": {
            "pop_quantile": 0.10,  # Top 10% population (90th percentile)
            "building_quantile": 0.10,  # Top 10% building coverage
            "road_quantile": 0.90,  # Not used
            "combined_min": 0.25
        },
        "loose": {
            "pop_quantile": 0.40,  # Top 15% population (85th percentile)
            "building_quantile": 0.40,  # Top 15% building coverage
            "road_quantile": 0.90,  # Not used
            "combined_min": 0.20
        }
    }
    
    params = strictness_params[urban_strictness]
    
    # Calculate thresholds
    pop_threshold = density["population"].quantile(1 - params["pop_quantile"])
    building_threshold = density["total_building_area_sqm"].quantile(1 - params["building_quantile"])
    road_threshold = density["road_density_km_per_sqkm"].quantile(1 - params["road_quantile"]) if use_road_density else 0
    
    print(f"\nStrictness: {urban_strictness.upper()}")
    print(f"Thresholds (top {params['pop_quantile']*100:.0f}% population, top {params['building_quantile']*100:.0f}% buildings):")
    print(f"  Population: >= {pop_threshold:.1f}")
    print(f"  Building Area: >= {building_threshold:.0f} m²")
    if use_road_density:
        print(f"  Road Density: >= {road_threshold:.2f} km/sq km")
    print(f"  Combined Score: >= {params['combined_min']:.3f}")
    
    # Calculate urban score for seed selection
    if use_road_density:
        density['urban_score'] = (
            density['population'] / density['population'].max() * 0.4 +
            density['total_building_area_sqm'] / density['total_building_area_sqm'].max() * 0.4 +
            density['road_density_km_per_sqkm'] / density['road_density_km_per_sqkm'].max() * 0.2
        )
    else:
        density['urban_score'] = (
            density['population'] / density['population'].max() * 0.6 +
            density['total_building_area_sqm'] / density['total_building_area_sqm'].max() * 0.4
        )
    
    # Function to check if cell meets urban criteria
    def meets_urban_criteria(row):
        pop_ok = row['population'] >= pop_threshold
        building_ok = row['total_building_area_sqm'] >= building_threshold
        road_ok = True
        if use_road_density:
            road_ok = row['road_density_km_per_sqkm'] >= road_threshold
        score_ok = row['urban_score'] >= params['combined_min']
        
        if urban_strictness == "strict" and use_road_density:
            return pop_ok and building_ok and road_ok and score_ok
        elif urban_strictness == "medium":
            return pop_ok and building_ok and score_ok
        else:  # loose
            return (pop_ok and building_ok) or score_ok
    
    # Find the best seed cell
    seed_idx = density['urban_score'].idxmax()
    seed_cell = density.loc[seed_idx]
    
    print(f"\nStarting from seed cell (index {seed_idx}) with score {seed_cell['urban_score']:.3f}")
    
    # Initialize BFS
    urban_cells_ids = {seed_cell['hex_id']}
    cells_to_process = deque([seed_cell])
    
    # Use spatial index for fast neighbor finding
    sindex = density.sindex
    
    # Main growing loop using BFS (much faster than previous approach)
    processed_count = 0
    while cells_to_process:
        current_cell = cells_to_process.popleft()
        processed_count += 1
        
        if processed_count % 100 == 0:
            print(f"Processed {processed_count} cells, urban area size: {len(urban_cells_ids)}")
        
        # Find neighboring cells using spatial index (faster)
        search_geom = current_cell.geometry.buffer(1)  # Small buffer for adjacency
        possible_matches_index = list(sindex.intersection(search_geom.bounds))
        possible_matches = density.iloc[possible_matches_index]
        
        # Check for actual adjacency
        neighbors = possible_matches[
            (possible_matches.geometry.touches(current_cell.geometry)) &
            (possible_matches['hex_id'] != current_cell['hex_id'])
        ]
        
        for idx, neighbor in neighbors.iterrows():
            # Check if neighbor meets criteria and hasn't been added
            if (neighbor['hex_id'] not in urban_cells_ids and 
                meets_urban_criteria(neighbor)):
                
                urban_cells_ids.add(neighbor['hex_id'])
                cells_to_process.append(neighbor)
    
    print(f"Initial BFS completed. Urban area: {len(urban_cells_ids)} cells")
    
    # Strategic gap filling phase - only fill gaps that connect to other urban areas
    print("\n--- Strategic gap filling phase ---")
    
    # Convert to set for faster lookups
    urban_set = set(urban_cells_ids)
    
    def find_potential_urban_clusters(radius=3):
        """Find clusters of cells that meet urban criteria but aren't connected to main area"""
        potential_clusters = []
        checked_cells = set()
        
        for idx, cell in density.iterrows():
            if (cell['hex_id'] not in urban_set and 
                cell['hex_id'] not in checked_cells and
                meets_urban_criteria(cell)):
                
                # Start a new cluster from this cell
                cluster = set()
                to_check = deque([cell['hex_id']])
                
                while to_check:
                    current_id = to_check.popleft()
                    if current_id in checked_cells:
                        continue
                        
                    checked_cells.add(current_id)
                    cluster.add(current_id)
                    
                    # Find neighbors of current cell
                    current_cell = density[density['hex_id'] == current_id].iloc[0]
                    search_geom = current_cell.geometry.buffer(1)
                    possible_matches_index = list(sindex.intersection(search_geom.bounds))
                    possible_matches = density.iloc[possible_matches_index]
                    
                    neighbors = possible_matches[
                        (possible_matches.geometry.touches(current_cell.geometry)) &
                        (possible_matches['hex_id'] != current_id) &
                        (~possible_matches['hex_id'].isin(urban_set)) &
                        (~possible_matches['hex_id'].isin(checked_cells))
                    ]
                    
                    for _, neighbor in neighbors.iterrows():
                        if meets_urban_criteria(neighbor):
                            to_check.append(neighbor['hex_id'])
                
                if len(cluster) >= 2:  # Only consider clusters of 2+ cells
                    potential_clusters.append(cluster)
        
        return potential_clusters
    
    def find_bridge_path(cluster, max_bridge_length=2):
        """Find if there's a short bridge path from main urban area to cluster"""
        # Find cells closest to main urban area from the cluster
        min_distance = float('inf')
        best_bridge = None
        
        for cluster_id in cluster:
            cluster_cell = density[density['hex_id'] == cluster_id].iloc[0]
            
            # Find shortest path to main urban area
            for urban_id in urban_set:
                urban_cell = density[density['hex_id'] == urban_id].iloc[0]
                distance = cluster_cell.geometry.distance(urban_cell.geometry)
                
                if distance < min_distance:
                    min_distance = distance
                    
                    # Try to find bridge cells
                    bridge_candidates = []
                    
                    # Look for cells between cluster and urban area
                    search_bounds = cluster_cell.geometry.union(urban_cell.geometry).bounds
                    possible_bridge_index = list(sindex.intersection(search_bounds))
                    
                    for bridge_idx in possible_bridge_index:
                        bridge_cell = density.iloc[bridge_idx]
                        if (bridge_cell['hex_id'] not in urban_set and 
                            bridge_cell['hex_id'] not in cluster):
                            
                            # Check if it's between cluster and urban area
                            dist_to_cluster = bridge_cell.geometry.distance(cluster_cell.geometry)
                            dist_to_urban = bridge_cell.geometry.distance(urban_cell.geometry)
                            
                            hex_size = np.sqrt(cluster_cell.geometry.area)
                            
                            if (dist_to_cluster <= hex_size * 1.5 and 
                                dist_to_urban <= hex_size * 1.5 and
                                # Bridge cell should have minimal development
                                (bridge_cell['population'] > 0 or bridge_cell['total_building_area_sqm'] > 0)):
                                bridge_candidates.append(bridge_cell['hex_id'])
                    
                    if len(bridge_candidates) <= max_bridge_length:
                        best_bridge = bridge_candidates
        
        return best_bridge
    
    # Find potential urban clusters
    potential_clusters = find_potential_urban_clusters()
    print(f"Found {len(potential_clusters)} potential urban clusters to connect")
    
    bridges_added = 0
    clusters_connected = 0
    
    for cluster in potential_clusters:
        bridge_path = find_bridge_path(cluster, max_bridge_length=2)
        
        if bridge_path is not None:
            # Add bridge cells and cluster to urban area
            urban_set.update(bridge_path)
            urban_set.update(cluster)
            bridges_added += len(bridge_path)
            clusters_connected += 1
            print(f"Connected cluster of {len(cluster)} cells with {len(bridge_path)} bridge cells")
    
    print(f"Connected {clusters_connected} clusters using {bridges_added} bridge cells")
    
    # Final small hole filling - only for cells completely surrounded
    print("\n--- Final hole filling (surrounded cells only) ---")
    holes_filled = 0
    
    for idx, cell in density.iterrows():
        if cell['hex_id'] not in urban_set:
            # Find neighbors using spatial index
            search_geom = cell.geometry.buffer(1)
            possible_matches_index = list(sindex.intersection(search_geom.bounds))
            possible_matches = density.iloc[possible_matches_index]
            
            neighbors = possible_matches[
                (possible_matches.geometry.touches(cell.geometry)) &
                (possible_matches['hex_id'] != cell['hex_id'])
            ]
            
            urban_neighbors = neighbors[neighbors['hex_id'].isin(urban_set)]
            total_neighbors = len(neighbors)
            urban_neighbor_count = len(urban_neighbors)
            
            # Only fill if completely surrounded (100% urban neighbors) and has some development
            if (total_neighbors > 0 and 
                urban_neighbor_count == total_neighbors and  # 100% surrounded
                urban_neighbor_count >= 3 and  # At least 3 neighbors
                (cell['population'] > 0 or cell['total_building_area_sqm'] > 0)):  # Some development
                
                urban_set.add(cell['hex_id'])
                holes_filled += 1
    
    if holes_filled > 0:
        print(f"Filled {holes_filled} completely surrounded holes")
    
    # Final connected component analysis to ensure single contiguous area
    print("\n--- Connected component analysis ---")
    
    if urban_set:
        urban_cells_temp = density[density['hex_id'].isin(urban_set)].copy()
        urban_cells_temp['component'] = 0
        component_count = 0
        unvisited_ids = set(urban_cells_temp['hex_id'])
        
        while unvisited_ids:
            component_count += 1
            seed_id = next(iter(unvisited_ids))
            stack = [seed_id]
            unvisited_ids.remove(seed_id)
            
            while stack:
                current_id = stack.pop()
                urban_cells_temp.loc[urban_cells_temp['hex_id'] == current_id, 'component'] = component_count
                
                # Find adjacent cells within current component
                current_geom = urban_cells_temp.loc[urban_cells_temp['hex_id'] == current_id, 'geometry'].iloc[0]
                search_geom = current_geom.buffer(1)
                possible_matches_index = list(sindex.intersection(search_geom.bounds))
                
                # Check for adjacency to unvisited urban cells
                for p_idx in possible_matches_index:
                    if p_idx < len(density):  # Valid index
                        candidate_id = density.iloc[p_idx]['hex_id']
                        if (candidate_id in unvisited_ids and 
                            density.iloc[p_idx].geometry.touches(current_geom)):
                            unvisited_ids.remove(candidate_id)
                            stack.append(candidate_id)
        
        # Keep only the largest component
        if component_count > 1:
            print(f"Found {component_count} components, keeping largest")
            largest_component = urban_cells_temp['component'].value_counts().idxmax()
            final_urban_ids = urban_cells_temp[urban_cells_temp['component'] == largest_component]['hex_id']
        else:
            final_urban_ids = urban_cells_temp['hex_id']
    else:
        final_urban_ids = []
    
    # Create final result
    if len(final_urban_ids) > 0:
        result = density[density['hex_id'].isin(final_urban_ids)].copy()
        result = result.drop(columns=['urban_score', 'hex_id'], errors='ignore')
        result = result.reset_index(drop=True)
        print(f"\nFinal contiguous urban area: {len(result)} cells")
        return result
    else:
        print("\nNo urban area identified")
        return gpd.GeoDataFrame()

## Run Urban Area Detection

The urban detection algorithm focuses on **population and building density** as primary indicators of urban development:

### Strictness Levels:
- **"strict"**: Uses all 3 metrics (population, buildings, roads) with moderate thresholds
  - Uses top 8% as seeds, requires strong performance in most metrics
  - Best for identifying dense urban cores with comprehensive infrastructure
  
- **"medium"**: Uses 2 metrics (population, buildings) - **RECOMMENDED**
  - Uses top 12% as seeds, requires both population AND building presence
  - Good balance for identifying developed urban areas
  
- **"loose"**: Uses 2 metrics (population, buildings) with lower thresholds
  - Uses top 20% as seeds, more flexible criteria
  - Captures suburban and lower-density development

### Key Features:
- **Development-Focused**: Prioritizes actual signs of urban development (people + buildings)
- **Road Density**: Only used in "strict" mode to refine high-density areas
- **Hole Filling**: Automatically fills gaps surrounded by urban cells
- **Multi-round Growth**: Progressive expansion with decreasing thresholds
- **Connectivity**: Ensures urban areas are spatially connected

In [48]:
# Run urban area detection with adjustable strictness
URBAN_STRICTNESS = "loose"  # Adjust this parameter to include more ("loose") or fewer ("strict") cells

# Clear any previous results
urban_cells = None

print(f"Running urban area detection (strictness: {URBAN_STRICTNESS})...")
urban_cells = run_growing_method(analysis_data.copy(), urban_strictness=URBAN_STRICTNESS)

# Calculate and display summary statistics
if not urban_cells.empty:
    total_pop = analysis_data['population'].sum()
    total_road_length = analysis_data['total_road_length_m'].sum()
    hex_area_sqm = analysis_data.geometry.iloc[0].area
    
    urban_pop = urban_cells['population'].sum()
    urban_pop_pct = (urban_pop / total_pop) * 100
    urban_area_pct = (len(urban_cells) / len(analysis_data)) * 100
    avg_road_density = urban_cells['road_density_km_per_sqkm'].mean()
    
    print(f"\n=== URBAN AREA SUMMARY (Strictness: {URBAN_STRICTNESS.upper()}) ===")
    print(f"Urban cells: {len(urban_cells):,} ({urban_area_pct:.1f}% of total area)")
    print(f"Urban population: {urban_pop:,.0f} ({urban_pop_pct:.1f}% of total)")
    print(f"Urban building area: {urban_cells['total_building_area_sqm'].sum():,.0f} m²")
    print(f"Average road density: {avg_road_density:.2f} km/sq km")
    print(f"Total road length: {urban_cells['total_road_length_m'].sum()/1000:.1f} km")
    
    print("\nAverage Urban Cell Metrics:")
    print(f"- Population per cell: {urban_cells['population'].mean():.1f}")
    print(f"- Building area per cell: {urban_cells['total_building_area_sqm'].mean():.0f} m²")
    print(f"- Road density per cell: {avg_road_density:.2f} km/sq km")
    
else:
    print("No urban cells identified")
    print("Try using 'loose' strictness or check your data thresholds")

Running urban area detection (strictness: loose)...
Running enhanced growing method (strictness: loose)...
Using 2 metrics: population, building area

Strictness: LOOSE
Thresholds (top 30% population, top 30% buildings):
  Population: >= 216.6
  Building Area: >= 72709 m²
  Combined Score: >= 0.250

Starting from seed cell (index 881) with score 0.821
Processed 100 cells, urban area size: 129
Processed 200 cells, urban area size: 224
Processed 300 cells, urban area size: 323
Processed 400 cells, urban area size: 420
Processed 500 cells, urban area size: 511
Initial BFS completed. Urban area: 579 cells

--- Strategic gap filling phase ---
Found 20 potential urban clusters to connect
Connected cluster of 2 cells with 2 bridge cells
Connected cluster of 4 cells with 0 bridge cells
Connected cluster of 4 cells with 2 bridge cells
Connected cluster of 3 cells with 0 bridge cells
Connected cluster of 3 cells with 2 bridge cells
Connected cluster of 2 cells with 0 bridge cells
Connected clust

## Visualize Results

In [49]:
# Visualize urban area results
if not urban_cells.empty:
    print(f"Visualizing {len(urban_cells)} urban cells...")
    
    urban_viz = urban_cells.to_crs("EPSG:4326")
    
    # Calculate quantiles for tooltip display
    urban_viz['pop_quantile'] = (urban_viz['population'].rank(pct=True) * 100).round(0).astype(int)
    urban_viz['building_quantile'] = (urban_viz['total_building_area_sqm'].rank(pct=True) * 100).round(0).astype(int)
    if 'road_density_km_per_sqkm' in urban_viz.columns:
        urban_viz['road_quantile'] = (urban_viz['road_density_km_per_sqkm'].rank(pct=True) * 100).round(0).astype(int)
    
    # Round values for cleaner tooltips (without 'rounded' in column names)
    urban_viz['population_display'] = urban_viz['population'].round(0).astype(int)
    urban_viz['building_count_display'] = urban_viz['building_count'].astype(int)
    urban_viz['building_area_display'] = urban_viz['total_building_area_sqm'].round(0).astype(int)
    
    # Calculate building coverage percentage
    hex_area_sqm = analysis_data.geometry.iloc[0].area
    urban_viz['building_coverage_pct'] = (urban_viz['total_building_area_sqm'] / hex_area_sqm * 100).round(0).astype(int)
    
    if 'road_density_km_per_sqkm' in urban_viz.columns:
        urban_viz['road_density_display'] = urban_viz['road_density_km_per_sqkm'].round(0).astype(int)
        urban_viz['road_length_display'] = urban_viz['total_road_length_m'].round(0).astype(int)
    
    # Prepare tooltip columns with quantiles and display values
    tooltip_cols = [
        "population_display", "pop_quantile",
        "building_count_display", "building_area_display", "building_quantile", 
        "building_coverage_pct"
    ]
    
    if 'road_density_km_per_sqkm' in urban_viz.columns:
        tooltip_cols.extend([
            "road_density_display", "road_quantile", "road_length_display"
        ])
    
    # Create background layer with all analysis cells
    all_cells_viz = analysis_data.to_crs("EPSG:4326")
    # Add quantiles and rounded values for tooltips
    all_cells_viz['pop_quantile'] = (all_cells_viz['population'].rank(pct=True) * 100).round(0).astype(int)
    all_cells_viz['building_quantile'] = (all_cells_viz['total_building_area_sqm'].rank(pct=True) * 100).round(0).astype(int)
    if 'road_density_km_per_sqkm' in all_cells_viz.columns:
        all_cells_viz['road_quantile'] = (all_cells_viz['road_density_km_per_sqkm'].rank(pct=True) * 100).round(0).astype(int)
    all_cells_viz['population_display'] = all_cells_viz['population'].round(0).astype(int)
    all_cells_viz['building_area_display'] = all_cells_viz['total_building_area_sqm'].round(0).astype(int)
    if 'road_density_km_per_sqkm' in all_cells_viz.columns:
        all_cells_viz['road_density_display'] = all_cells_viz['road_density_km_per_sqkm'].round(0).astype(int)

    # Tooltip for all analysis cells
    all_cells_tooltip = [
        "population_display", "pop_quantile",
        "building_area_display", "building_quantile"
    ]
    if 'road_density_km_per_sqkm' in all_cells_viz.columns:
        all_cells_tooltip.extend(["road_density_display", "road_quantile"])
    
    # Create base map with all analysis cells (background layer, hidden by default)
    m = all_cells_viz.explore(
        color="lightgrey",
        tooltip=all_cells_tooltip,
        popup=False,
        style_kwds=dict(
            fillColor="lightgrey",
            color="darkgrey", 
            fillOpacity=0.5,
            weight=1,
            opacity=0.8
        ),
        name="All Analysis Cells"
    )
    
    # Add population layer (default)
    urban_viz.explore(
        m=m,  # Add to existing map
        column="population",
        cmap="viridis",
        tooltip=tooltip_cols,
        popup=True,
        legend=True,
        legend_kwds=dict(caption="Population"),
        style_kwds=dict(fillOpacity=0.7, weight=0.5),
        name="Population Density"
    )
    
    # Add building density layer (hidden by default)
    urban_viz.explore(
        m=m,  # Add to existing map
        column="total_building_area_sqm",
        cmap="plasma",
        tooltip=tooltip_cols,
        popup=True,
        legend=True,
        legend_kwds=dict(caption="Building Area (m²)"),
        style_kwds=dict(fillOpacity=0.7, weight=0.5),
        name="Building Density"
    )
    
    # Add road density layer if available (hidden by default)
    if 'road_density_km_per_sqkm' in urban_viz.columns:
        urban_viz.explore(
            m=m,  # Add to existing map
            column="road_density_km_per_sqkm",
            cmap="inferno",
            tooltip=tooltip_cols,
            popup=True,
            legend=True,
            legend_kwds=dict(caption="Road Density (km/sq km)"),
            style_kwds=dict(fillOpacity=0.7, weight=0.5),
            name="Road Density"
        )
    
    # Add layer control and configure visibility
    layer_control = folium.LayerControl()
    layer_control.add_to(m)
    
    # Hide all layers except Population Density by default
    for layer_name in m._children:
        if hasattr(m._children[layer_name], 'layer_name'):
            if m._children[layer_name].layer_name in ["All Analysis Cells", "Building Density", "Road Density"]:
                m._children[layer_name].show = False
    
    print(f"Interactive map created with {len(tooltip_cols)} tooltip fields")
    print("Layers available:")
    print("- All Analysis Cells (background, hidden by default)")
    print("- Population Density (visible by default)")
    print("- Building Density (hidden by default)")
    if 'road_density_km_per_sqkm' in urban_viz.columns:
        print("- Road Density (hidden by default)")
    
    display(m)
else:
    print("No urban area to visualize")

Visualizing 600 urban cells...
Interactive map created with 9 tooltip fields
Layers available:
- All Analysis Cells (background, hidden by default)
- Population Density (visible by default)
- Building Density (hidden by default)
- Road Density (hidden by default)
Interactive map created with 9 tooltip fields
Layers available:
- All Analysis Cells (background, hidden by default)
- Population Density (visible by default)
- Building Density (hidden by default)
- Road Density (hidden by default)


## Save Results

In [31]:
# Save urban area results
if not urban_cells.empty:
    print(f"Saving results for {len(urban_cells)} urban cells...")
    
    # Define output paths
    method = "growing"
    output_dir = Path(DATA_DIR)
    urban_cells_geojson = output_dir / f"urban_cells_{CITY_SHORT_NAME}_{method}.geojson"
    urban_gpkg = output_dir / "urban_areas.gpkg"
    analysis_gpkg = output_dir / "population_density.gpkg"
    
    cells_layer = f"urban_cells_{CITY_SHORT_NAME}_{method}"
    hull_layer = f"urban_area_{CITY_SHORT_NAME}_{method}"
    analysis_layer = f"population_density_with_buildings_roads_{CITY_SHORT_NAME}"
    
    # Convert to WGS84 for saving
    urban_save = urban_cells.to_crs("EPSG:4326")
    
    # Save individual cells
    urban_save.to_file(str(urban_cells_geojson), driver="GeoJSON")
    urban_save.to_file(str(urban_gpkg), layer=cells_layer, driver="GPKG")
    
    # Create and save urban area hull
    urban_hull = gpd.GeoDataFrame(
        [urban_cells.unary_union],
        columns=["geometry"],
        crs=urban_cells.crs
    ).to_crs("EPSG:4326")
    
    urban_hull.to_file(str(urban_gpkg), layer=hull_layer, driver="GPKG")
    
    # Save analysis dataset
    analysis_data.to_file(str(analysis_gpkg), layer=analysis_layer, driver="GPKG")
    
    print("Results saved to:")
    print(f"- Urban cells (GeoJSON): {urban_cells_geojson}")
    print(f"- Urban cells (GPKG): {urban_gpkg}/{cells_layer}")
    print(f"- Urban hull (GPKG): {urban_gpkg}/{hull_layer}")
    print(f"- Analysis data: {analysis_gpkg}/{analysis_layer}")
else:
    print("No urban area to save")

Saving results for 654 urban cells...
Results saved to:
- Urban cells (GeoJSON): data\urban_cells_oslo_growing.geojson
- Urban cells (GPKG): data\urban_areas.gpkg/urban_cells_oslo_growing
- Urban hull (GPKG): data\urban_areas.gpkg/urban_area_oslo_growing
- Analysis data: data\population_density.gpkg/population_density_with_buildings_roads_oslo


## Final Summary

In [32]:
# Print comprehensive summary
print(f"\n{'=' * 60}")
print(f"URBAN AREA ANALYSIS SUMMARY FOR {CITY_NAME.upper()}")
print(f"{'=' * 60}")

print("\nInput Data:")
print(f"- Total hexagons analyzed: {len(analysis_data):,}")
print(f"- Total population: {analysis_data['population'].sum():,}")
print(f"- Total building area: {analysis_data['total_building_area_sqm'].sum():,.0f} m²")
print(f"- Total buildings: {analysis_data['building_count'].sum():,}")

if 'road_density_km_per_sqkm' in analysis_data.columns:
    total_roads = analysis_data['total_road_length_m'].sum() / 1000
    avg_density = analysis_data['road_density_km_per_sqkm'].mean()
    print(f"- Total road length: {total_roads:.1f} km")
    print(f"- Average road density: {avg_density:.2f} km/sq km")

if not urban_cells.empty:
    urban_pop_pct = (urban_cells['population'].sum() / analysis_data['population'].sum()) * 100
    urban_area_pct = (len(urban_cells) / len(analysis_data)) * 100
    metrics_used = 3 if 'road_density_km_per_sqkm' in urban_cells.columns else 2
    
    print("\nUrban Area Results:")
    print("- Algorithm: Region growing with hole filling")
    print(f"- Metrics used: {metrics_used} (population, building area" + (", road density" if metrics_used == 3 else "") + ")")
    print(f"- Urban cells: {len(urban_cells):,} ({urban_area_pct:.1f}% of total area)")
    print(f"- Urban population: {urban_cells['population'].sum():,} ({urban_pop_pct:.1f}% of total)")
    
    urban_building_area = urban_cells['total_building_area_sqm'].sum()
    urban_building_pct = (urban_building_area / analysis_data['total_building_area_sqm'].sum()) * 100
    print(f"- Urban building area: {urban_building_area:,.0f} m² ({urban_building_pct:.1f}% of total)")
    
    if 'road_density_km_per_sqkm' in urban_cells.columns:
        urban_road_length = urban_cells['total_road_length_m'].sum() / 1000
        urban_road_pct = (urban_road_length / total_roads) * 100
        urban_avg_density = urban_cells['road_density_km_per_sqkm'].mean()
        print(f"- Urban road length: {urban_road_length:.1f} km ({urban_road_pct:.1f}% of total)")
        print(f"- Urban road density: {urban_avg_density:.2f} km/sq km")
else:
    print("\nNo urban area identified")

print(f"\n{'=' * 60}")
print("ANALYSIS COMPLETE")
print(f"{'=' * 60}")


URBAN AREA ANALYSIS SUMMARY FOR OSLO, NORWAY

Input Data:
- Total hexagons analyzed: 2,450
- Total population: 972,349.0
- Total building area: 195,540,654 m²
- Total buildings: 330,797
- Total road length: 9374.4 km
- Average road density: 9.41 km/sq km

Urban Area Results:
- Algorithm: Region growing with hole filling
- Metrics used: 3 (population, building area, road density)
- Urban cells: 654 (26.7% of total area)
- Urban population: 830,722.0 (85.4% of total)
- Urban building area: 150,020,167 m² (76.7% of total)
- Urban road length: 5586.4 km (59.6% of total)
- Urban road density: 21.01 km/sq km

ANALYSIS COMPLETE
